# `mlc-python`

[MLC-Python](https://github.com/mlc-ai/mlc-python) 是一款以 Python 为核心的工具包，它通过提供 Python 风格的数据类、结构感知工具以及基于 Python 的文本格式，极大地简化了 AI 编译器、运行时环境和复合 AI 系统的开发流程。

除了纯粹的 Python 环境外，MLC 还原生支持与 C++ 插件的零拷贝互操作，使得从纯 Python 开发到混合开发乃至无 Python 依赖的工程实践过渡变得顺畅无阻。

## 📥 安装

```bash
pip install -U mlc-python
```

## 🔑 关键特性

### 🏗️ 使用 MLC 数据类定义 IRs

MLC提供了 Python 风格的数据类：

In [1]:
import mlc.dataclasses as mlcd

@mlcd.py_class("demo.MyClass")
class MyClass(mlcd.PyClass):
  a: int
  b: str
  c: float | None

instance = MyClass(12, "test", c=None)

In [2]:
instance

demo.MyClass(a=12, b='test', c=None)

**类型安全**。MLC 数据类通过 Cython 和 C++ 强制执行严格的类型检查。

In [3]:
instance.c = 10
instance

demo.MyClass(a=12, b='test', c=10.0)

In [4]:
instance.c = "wrong type"

TypeError: must be real number, not str

In [5]:
instance.non_exist = 1

AttributeError: 'MyClass' object has no attribute 'non_exist'

**序列化**。MLC 数据类支持 {mod}`pickle` 序列化和 JSON 序列化。

In [6]:
MyClass.from_json(instance.json())

demo.MyClass(a=12, b='test', c=10.0)

In [7]:
import pickle
pickle.loads(pickle.dumps(instance))

demo.MyClass(a=12, b='test', c=10.0)

### 🐍 为 IRs 设计基于 Python 的文本格式

**打印机**。MLC 查找方法 `__ir_print__` 以将 IR 节点转换为 Python AST：

**[[示例](https://github.com/mlc-ai/mlc-python/blob/main/python/mlc/testing/toy_ir/ir.py)]**。将玩具 IR 定义复制到 REPL 中，然后创建下面的 `Func` 节点：

In [8]:
from mlc.testing.toy_ir.ir import Var, Func, Assign, Add
a, b, c, d, e = Var("a"), Var("b"), Var("c"), Var("d"), Var("e")
f = Func(
    "f", [a, b, c],
    stmts=[
        Assign(lhs=d, rhs=Add(a, b)),  # d = a + b
        Assign(lhs=e, rhs=Add(d, c)),  # e = d + c
    ],
    ret=e
)

方法 {func}`mlc.printer.to_python` 将 IR 节点转换为基于 Python 的文本；

In [9]:
import mlc
print(mlc.printer.to_python(f))  # 字符串化为Python

def f(a, b, c):
  d = a + b
  e = d + c
  return e


方法 `mlc.printer.print_python` 进一步以适当的语法高亮渲染文本。

In [10]:
mlc.printer.print_python(f) # 语法高亮

**AST 解析器**。MLC 提供了一套简洁的 API，用于利用 Python 的 AST 模块实现解析器，包括：
- 检查 API，用于获取 Python 类或函数的源代码及其捕获的变量；
- 变量管理 API，有助于正确处理作用域；
- AST 片段评估 API；
- 错误渲染 API。

**[[示例](https://github.com/mlc-ai/mlc-python/blob/main/python/mlc/testing/toy_ir/parser.py)]**。借助 MLC API，可以用 100 行代码实现解析器，用于解析上述由 `__ir_printer__` 定义的 Python 文本格式。

### 🎯 使用 MLC 结构感知工具测试 IRs

通过在 IR 定义中标注 `structure`，MLC 支持结构相等性和结构哈希，以检测 IR 之间的结构等价性：

使用 `structure` 定义玩具 IR：

In [11]:
import mlc.dataclasses as mlcd

@mlcd.py_class
class Expr(mlcd.PyClass):
    def __add__(self, other):
        return Add(a=self, b=other)

@mlcd.py_class(structure="nobind")
class Add(Expr):
    a: Expr
    b: Expr

@mlcd.py_class(structure="var")
class Var(Expr):
    name: str = mlcd.field(structure=None) # excludes `name` from defined structure

@mlcd.py_class(structure="bind")
class Let(Expr):
    rhs: Expr
    lhs: Var = mlcd.field(structure="bind") # `Let.lhs` is the def-site
    body: Expr

**结构相等性**。成员方法 `eq_s` 用于比较由MLC的结构化数据类表示的两个IR（中间表示）的结构相等性（即 alpha 等价）。

In [12]:
x, y, z = Var("x"), Var("y"), Var("z")
L1 = Let(rhs=x + y, lhs=z, body=z)  # let z = x + y; z
L2 = Let(rhs=y + z, lhs=x, body=x)  # let x = y + z; x
L3 = Let(rhs=x + x, lhs=z, body=z)  # let z = x + x; z
L1.eq_s(L2)

True

In [13]:
L1.eq_s(L3, assert_mode=True)

ValueError: Structural equality check failed at {root}.rhs.b: Inconsistent binding. RHS has been bound to a different node while LHS is not bound

**结构哈希**。MLC 数据类的结构可以通过 `hash_s` 进行哈希计算，这保证了如果两个数据类是 alpha 等价的，它们将具有相同的结构哈希值：

In [14]:
L1_hash, L2_hash, L3_hash = L1.hash_s(), L2.hash_s(), L3.hash_s()
assert L1_hash == L2_hash
assert L1_hash != L3_hash

### ⚡ 逐步迁移到 C++ 并使用 MLC 插件

(🚧 正在建设中)

MLC 无缝支持与 C++ 插件的零拷贝双向互操作性，且无需额外依赖。通过逐步迁移类和方法，可以将纯 Python 原型过渡到混合开发或无 Python 开发模式。

## ⛽ 开发

### ⚙️ 可编辑构建

```bash
pip install --verbose --editable ".[dev]"
pre-commit install
```


### 🎡 构建 Wheels

本项目使用 `cibuildwheel` 来构建跨平台的 wheels。更多详情请参阅 `.github/workflows/wheels.yml`。